In [8]:
import pickle
import pandas as pd
import numpy as np

In [9]:
import xgboost as xgb
model_path = "model.None"
model = xgb.Booster()
model.load_model(model_path)

In [2]:
dv_path = "dv.bin"
with open(dv_path, 'rb') as f_out:
    dv = pickle.load(f_out)

In [6]:
scaler_path = "scaler.bin"
with open(scaler_path, 'rb') as f_out:
    scaler = pickle.load(f_out)

In [10]:
def preprocess(data):
    """Preprocessing of the data"""
    # turn json input to dataframe
    data = pd.DataFrame([data])

    # define numerical and categorical features
    numerical = ["X1", "X2", "X3", "X4", "X5", "X7"]
    categorical = ["X6", "X8"]

    # preprocess numerical features
    X_num = scaler.transform(data[numerical])
    # preprocess categorical features
    data[categorical] = data[categorical].astype("string")
    X_dicts = data[categorical].to_dict(orient="records")
    X_cat = dv.transform(X_dicts)
    # concatenate both
    X = np.concatenate((X_num, X_cat), axis=1)

    return X


def predict(X):
    """make predictions"""
    pred = model.predict(X)
    print('prediction', pred[0])
    return float(pred[0])

In [17]:
def main(input_data):
    """request input, preprocess it and make prediction"""
    features = preprocess(input_data)
    features_2 = xgb.DMatrix(features)
    pred = predict(features_2)

    result = {'heat load': pred}

    return result


In [18]:
input_example = {
    "X1": 0.98,
    "X2": 514.50,
    "X3": 294.00,
    "X4": 110.25,
    "X5": 7.00,
    "X6": 2,
    "X7": 0.00,
    "X8": 0,
}

main(input_example)

prediction 15.648413


{'heat load': 15.648412704467773}